# Data Processing

In [102]:
import pandas as pd
import numpy as np
import folium
import geopandas as gpd
from shapely.geometry import Point

In [75]:
trees = pd.read_csv('data/2015_Street_Tree_Census_-_Tree_Data.csv')

In [76]:
trees.head()

tree_id  block_id  created_at  tree_dbh  stump_diam curb_loc status health  \
0   180683    348711  08/27/2015         3           0   OnCurb  Alive   Fair   
1   200540    315986  09/03/2015        21           0   OnCurb  Alive   Fair   
2   204026    218365  09/05/2015         3           0   OnCurb  Alive   Good   
3   204337    217969  09/05/2015        10           0   OnCurb  Alive   Good   
4   189565    223043  08/30/2015        21           0   OnCurb  Alive   Good   

                            spc_latin       spc_common  ...  boro_ct  \
0                         Acer rubrum        red maple  ...  4073900   
1                   Quercus palustris          pin oak  ...  4097300   
2  Gleditsia triacanthos var. inermis      honeylocust  ...  3044900   
3  Gleditsia triacanthos var. inermis      honeylocust  ...  3044900   
4                     Tilia americana  American linden  ...  3016500   

      state   latitude  longitude         x_sp         y_sp council district  \
0  New York  40.723092 -73.844215  1027431.148  202756.7687             29.0   
1  New York  40.794111 -73.818679  1034455.701  228644.8374             19.0   
2  New York  40.717581 -73.936608  1001822.831  200716.8913             34.0   
3  New York  40.713537 -73.934456  1002420.358  199244.2531             34.0   
4  New York  40.666778 -73.975979   990913.775  182202.4260             39.0   

  census tract        bin           bbl  
0        739.0  4052307.0  4.022210e+09  
1        973.0  4101931.0  4.044750e+09  
2        449.0  3338310.0  3.028870e+09  
3        449.0  3338342.0  3.029250e+09  
4        165.0  3025654.0  3.010850e+09  

[5 rows x 45 columns]

In [78]:
trees.shape

(683788, 45)

In [2]:
temp = pd.read_csv('data/Hyperlocal_Temperature_Monitoring.csv')
temp.head()

Sensor.ID    AirTemp         Day  Hour   Latitude  Longitude  Year  \
0  Bk-BR_01  71.189000  06/15/2018     1  40.666205  -73.91691  2018   
1  Bk-BR_01  70.243333  06/15/2018     2  40.666205  -73.91691  2018   
2  Bk-BR_01  69.392667  06/15/2018     3  40.666205  -73.91691  2018   
3  Bk-BR_01  68.263167  06/15/2018     4  40.666205  -73.91691  2018   
4  Bk-BR_01  67.114000  06/15/2018     5  40.666205  -73.91691  2018   

  Install.Type   Borough ntacode  
0  Street Tree  Brooklyn    BK81  
1  Street Tree  Brooklyn    BK81  
2  Street Tree  Brooklyn    BK81  
3  Street Tree  Brooklyn    BK81  
4  Street Tree  Brooklyn    BK81

In [92]:
unique_locations = temp.groupby(['Latitude','Longitude']).count().reset_index(0).reset_index(0)[['Latitude','Longitude']]

In [103]:
tree_locs = [Point(row['latitude'],row['longitude']) for _,row in trees.iterrows()]
temp_locs = [Point(row['Latitude'],row['Longitude']) for _,row in unique_locations.iterrows()]

In [ ]:
def get_gdf(locs):
    

In [151]:
tl_df = gpd.GeoDataFrame({'geometry': temp_locs}, crs='EPSG:4326')
tl_df = tl_df.to_crs('EPSG:2263')

In [152]:
tl_df

geometry
0    POINT (140639851.101 -12967631.490)
1    POINT (140610641.915 -12959561.274)
2    POINT (140606507.117 -12957609.340)
3    POINT (140622655.975 -12961871.450)
4    POINT (140639989.328 -12966458.012)
..                                   ...
430  POINT (140155183.882 -12435122.528)
431  POINT (140135298.739 -12429820.427)
432  POINT (140144046.436 -12431810.503)
433  POINT (140140125.291 -12429826.339)
434  POINT (140155359.435 -12432890.471)

[435 rows x 1 columns]

In [153]:
points_df = gpd.GeoDataFrame({'geometry': tree_locs}, crs='EPSG:4326')

In [154]:
points_df = points_df.to_crs('EPSG:2263')

In [155]:
out = points_df.distance(tl_df.iloc[[0]*trees.shape[0]].reset_index(0).drop(columns='index'))

In [161]:
sum(out < 10000)

321

In [30]:
days = temp.groupby(['Latitude','Longitude','Day'])

In [31]:
days

Sensor.ID  AirTemp  Hour  Year  Install.Type  \
Latitude  Longitude  Day                                                        
40.646738 -73.951234 06/15/2018         23       23    23    23            23   
                     06/15/2019         23       23    23    23            23   
                     06/16/2018         24       24    24    24            24   
                     06/16/2019         24       24    24    24            24   
                     06/17/2018         24       24    24    24            24   
...                                    ...      ...   ...   ...           ...   
40.884616 -73.849168 10/11/2018         24       24    24    24            24   
                     10/12/2018         24       24    24    24            24   
                     10/13/2018         24       24    24    24            24   
                     10/14/2018         24       18    24    24            24   
                     10/15/2018         21       21    21    21            21   

                                 Borough  ntacode  
Latitude  Longitude  Day                           
40.646738 -73.951234 06/15/2018       23       23  
                     06/15/2019       23       23  
                     06/16/2018       24       24  
                     06/16/2019       24       24  
                     06/17/2018       24       24  
...                                  ...      ...  
40.884616 -73.849168 10/11/2018       24       24  
                     10/12/2018       24       24  
                     10/13/2018       24       24  
                     10/14/2018       24       24  
                     10/15/2018       21       21  

[87500 rows x 7 columns]

In [70]:
cuts = pd.cut(list(range(int(temp['AirTemp'].min()),int(temp['AirTemp'].max()) + 1)),5)

In [72]:
cuts.categories

IntervalIndex([(45.932, 59.6], (59.6, 73.2], (73.2, 86.8], (86.8, 100.4], (100.4, 114.0]],
              closed='right',
              dtype='interval[float64]')

In [45]:
colors = ['#00f4ff','#00ff6a','#F8ff00','#Ffa600','#Ff0000']

In [51]:
airtemp = temp.groupby(['Latitude','Longitude','Hour']).agg({'AirTemp':np.max})

In [52]:
airtemp = airtemp.reset_index(0).reset_index(0).reset_index(0)

In [53]:
airtemp

Hour  Longitude   Latitude    AirTemp
0         0 -73.951234  40.646738  90.495000
1         1 -73.951234  40.646738  89.385333
2         2 -73.951234  40.646738  87.939333
3         3 -73.951234  40.646738  87.133167
4         4 -73.951234  40.646738  86.572500
...     ...        ...        ...        ...
10435    19 -73.849168  40.884616  93.528167
10436    20 -73.849168  40.884616  90.682500
10437    21 -73.849168  40.884616  89.446167
10438    22 -73.849168  40.884616  88.702667
10439    23 -73.849168  40.884616  87.840500

[10440 rows x 4 columns]

In [62]:
(int(temp['AirTemp'].max()) + 1 - int(temp['AirTemp'].min()))/5

13.8

In [166]:
Hour = 16
NYC_COORD = [40.7128, -74.0059]
map_nyc = folium.Map(location=NYC_COORD, zoom_start=12, 
tiles='cartodbpositron', width=800, height=800)
for _,row in trees.sample(int(10e3)).iterrows():    
    folium.CircleMarker(location=(row['latitude'], row['longitude']),radius=1).add_to(map_nyc)
map_nyc

In [74]:
Hour = 16
NYC_COORD = [40.7128, -74.0059]
map_nyc = folium.Map(location=NYC_COORD, zoom_start=12, 
tiles='cartodbpositron', width=800, height=800)
for _,row in airtemp[airtemp['Hour'] == Hour].iterrows():
    html = str(row['AirTemp'])

    iframe = folium.IFrame(html,
                           width=100,
                           height=100)

    popup = folium.Popup(iframe,
                         max_width=100)

    c = 0
    for i in range(len(cuts.categories)):
        if row['AirTemp'] in cuts.categories[i]:
            c =i
    
    folium.CircleMarker(location=(row['Latitude'], row['Longitude']),color=colors[c],radius=1).add_to(map_nyc)
map_nyc